# FinBERT Notebook

FinBERT pre-trained language model for financial sentiment analysis.
Bibliography : https://github.com/ProsusAI/finBERT

## Modules 

In [1]:
import os
from pathlib import Path
import re
import datetime

In [2]:
os.chdir(os.getcwd() + r'\finbert')
project_dir = Path.cwd()
project_dir #WindowsPath('C:/Users/flori/Documents/projetBilel/gan/StockPricePredictionWithGan/News/sentimentAnalysis/finbert')

WindowsPath('C:/Users/flori/Documents/projetBilel/gan/StockPricePredictionWithGan/News/sentimentAnalysis/finbert')

In [3]:
import sys
import pandas as pd
pd.set_option('max_colwidth', -1)

from transformers import BertForSequenceClassification

from finbert.finbert import *
import finbert.utils as tools

import nltk
from nltk.tokenize import sent_tokenize
nltk.download('punkt')

import csv

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\flori\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


### Get predictions

With the `predict` function, given a piece of text, we split it into a list of sentences and then predict sentiment for each sentence. The output is written into a dataframe. Predictions are represented in three different columns: 

1) `logit`: probabilities for each class

2) `prediction`: predicted label

3) `sentiment_score`: sentiment score calculated as: probability of positive - probability of negative

In [4]:
filename = project_dir.parent.parent.parent /'Data'/'articles.csv'
data = pd.read_csv(filename)

# initializing the titles list 
titles = []
dates = []

for index, row in data.iterrows():
    dates.append(row['Article_Date'])
    titles.append(row['Article_Title'])

In [5]:
# keep only articles before 2022
for i in range(len(titles)):
    if re.search('\d{4}', dates[i]):
        indexUntil2021 = i
        break
titles = titles[indexUntil2021:]
dates = dates[indexUntil2021:]

assert len(dates) == len(titles), 'error'
print(len(titles))

3536


In [6]:
titles

['House Speaker Nancy Pelosi buys millions of dollars in call options in Google, Disney, others',
 "Nasdaq could rise 20% next year, Wall Street underestimating growth - Wedbush's Dan Ives",
 'Advanced Micro Devices, P&G latest to pull out of CES as COVID-19 cases surge',
 "Amazon, Facebook's Meta named top Internet picks by Baird for 2022",
 'Facebook tried to stem leaks, pit politicians against one another - WSJ',
 'ProShares plans to enter the metaverse market with a new ETF',
 'Amazon, Meta and Uber listed among top tech picks for 2022 at Evercore',
 'Meta Platforms surges on signs of strong Oculus holiday demand',
 'Apple hires Meta Platforms AR comms head as headset release nears: report',
 "Hold cash for 2022? Satori's Dan Niles outlines dreary investment outlook for next year",
 "What are MKM Partners 'Black Swan' Internet predictions for 2022?",
 'Amazon, Meta, Twitter among firms to scrap in-person plans for CES',
 'Meta hits UBS list of most crowded trades, most megacaps sti

In [7]:
cl_path = project_dir/'models'/'classifier_model'/'finbert-sentiment'
model = BertForSequenceClassification.from_pretrained(cl_path, cache_dir=None, num_labels=3)

In [8]:
# make predictions
sentiment_scores = []

for i in range(len(titles)):
    result = predict(titles[i], model)
    sentiment_scores.append(result['sentiment_score'].mean())
    print(i, titles[i])

01/29/2022 11:28:06 - INFO - finbert.utils -   *** Example ***
01/29/2022 11:28:06 - INFO - finbert.utils -   guid: 0
01/29/2022 11:28:06 - INFO - finbert.utils -   tokens: [CLS] house speaker nancy pe ##los ##i buys millions of dollars in call options in google , disney , others [SEP]
01/29/2022 11:28:06 - INFO - finbert.utils -   input_ids: 101 2160 5882 7912 21877 10483 2072 23311 8817 1997 6363 1999 2655 7047 1999 8224 1010 6373 1010 2500 102 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
01/29/2022 11:28:06 - INFO - finbert.utils -   attention_mask: 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
01/29/2022 11:28:06 - INFO - finbert.utils -   token_type_ids: 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
01/29/2022 11:28:06 - INFO - finbert.utils -   label: None (id = 9090)
01/29/2022

0 House Speaker Nancy Pelosi buys millions of dollars in call options in Google, Disney, others


01/29/2022 11:28:07 - INFO - finbert.utils -   *** Example ***
01/29/2022 11:28:07 - INFO - finbert.utils -   guid: 0
01/29/2022 11:28:07 - INFO - finbert.utils -   tokens: [CLS] nas ##da ##q could rise 20 % next year , wall street under ##est ##imating growth - wed ##bush ' s dan ives [SEP]
01/29/2022 11:28:07 - INFO - finbert.utils -   input_ids: 101 17235 2850 4160 2071 4125 2322 1003 2279 2095 1010 2813 2395 2104 4355 22835 3930 1011 21981 22427 1005 1055 4907 23945 102 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
01/29/2022 11:28:07 - INFO - finbert.utils -   attention_mask: 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
01/29/2022 11:28:07 - INFO - finbert.utils -   token_type_ids: 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
01/29/2022 11:28:07 - INFO - finbert.utils -   label: None (i

1 Nasdaq could rise 20% next year, Wall Street underestimating growth - Wedbush's Dan Ives


01/29/2022 11:28:08 - INFO - finbert.utils -   *** Example ***
01/29/2022 11:28:08 - INFO - finbert.utils -   guid: 0
01/29/2022 11:28:08 - INFO - finbert.utils -   tokens: [CLS] advanced micro devices , p & g latest to pull out of ce ##s as co ##vid - 19 cases surge [SEP]
01/29/2022 11:28:08 - INFO - finbert.utils -   input_ids: 101 3935 12702 5733 1010 1052 1004 1043 6745 2000 4139 2041 1997 8292 2015 2004 2522 17258 1011 2539 3572 12058 102 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
01/29/2022 11:28:08 - INFO - finbert.utils -   attention_mask: 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
01/29/2022 11:28:08 - INFO - finbert.utils -   token_type_ids: 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
01/29/2022 11:28:08 - INFO - finbert.utils -   label: None (id = 9090)
01/29/2022 11:28:

...

3533 Facebook (NASDAQ:FB) deserves a valuation of $75B, not $100B, suggests Henry Blodget. While...


01/29/2022 12:49:06 - INFO - finbert.utils -   *** Example ***
01/29/2022 12:49:06 - INFO - finbert.utils -   guid: 0
01/29/2022 12:49:06 - INFO - finbert.utils -   tokens: [CLS] " it is the out ##lier , " writes fortune ' s dan prima ##ck of facebook ( nas ##da ##q : f ##b ) . [SEP]
01/29/2022 12:49:06 - INFO - finbert.utils -   input_ids: 101 1000 2009 2003 1996 2041 14355 1010 1000 7009 7280 1005 1055 4907 21111 3600 1997 9130 1006 17235 2850 4160 1024 1042 2497 1007 1012 102 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
01/29/2022 12:49:06 - INFO - finbert.utils -   attention_mask: 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
01/29/2022 12:49:06 - INFO - finbert.utils -   token_type_ids: 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
01/29/2022 12:49:06 - INFO - finbert.utils -   label: None (id

3534 "It is the outlier," writes Fortune's Dan Primack of Facebook (NASDAQ:FB). "The type of peerless...


01/29/2022 12:49:07 - INFO - finbert.utils -   *** Example ***
01/29/2022 12:49:07 - INFO - finbert.utils -   guid: 0
01/29/2022 12:49:07 - INFO - finbert.utils -   tokens: [CLS] " facebook ' s ( nas ##da ##q : f ##b ) float : a lesson in how to make $ 5 ##b and not ce ##de any control , " t ##wee ##ts . . . [SEP]
01/29/2022 12:49:07 - INFO - finbert.utils -   input_ids: 101 1000 9130 1005 1055 1006 17235 2850 4160 1024 1042 2497 1007 14257 1024 1037 10800 1999 2129 2000 2191 1002 1019 2497 1998 2025 8292 3207 2151 2491 1010 1000 1056 28394 3215 1012 1012 1012 102 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
01/29/2022 12:49:07 - INFO - finbert.utils -   attention_mask: 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
01/29/2022 12:49:07 - INFO - finbert.utils -   token_type_ids: 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0

3535 "Facebook's (NASDAQ:FB) float: a lesson in how to make $5B and not cede any control," tweets...


In [9]:
def transform_dates(string):
    if string.find('.') != -1:
        newFormat = '{}-{}-{}'.format(string[14:18], string[5:8], string[10:12])
    else:
        newFormat = '{}-{}-{}'.format(string[13:17], string[5:8], string[9:11])
    return datetime.datetime.strptime(newFormat, '%Y-%b-%d').date().strftime('%Y-%m-%d')

In [10]:
dataWithPred = pd.DataFrame({'Article_Date': dates,'Sentiment_Score': sentiment_scores})

# dates to the good format
dataWithPred['Article_Date'] = dataWithPred['Article_Date'].apply(transform_dates)

# mean if several articles have the same date
dataGrouped = dataWithPred.groupby(['Article_Date']).mean().reset_index()

# sort by date value
dataGrouped['Article_Date'] = pd.to_datetime(dataGrouped['Article_Date'])
dataSorted = dataGrouped.sort_values(by='Article_Date')

dataSorted.to_csv(project_dir.parent.parent.parent /'Data'/'articles_Sentiment_Scores.csv')